In [1]:
import django
import os
import pandas as pd
import numpy as np
import html
import namedentities as ne
from old_database.modules_webpage import entry_to_dict #read_publications, read_addresses, read_seminars
import time

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
#from research.models import Publication


#from home.models import Room, Country, Title_full, Gender, Status
from internal.models import Member
from external.models import Presentation
from home.models import Event_type, Presentation_type
#from teaching.models import Seminar

# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()

#import gender_guesser.detector as gender
import re


## Write old papers database

In [2]:
def read_addresses(file_name):
    
    with open(file_name, 'r',encoding='utf-8',errors='replace') as file:
            content = file.read() 
    all_entries = content.split('enditem')
    
    for entry in all_entries:
        dictio = entry_to_dict(entry)
        if dictio != {}:
            try:
                df = df.append(dictio, ignore_index=True)     # append new entry to DF
            except:
                df = pd.DataFrame(dictio, index=[0])          # first time create the DF
    df = df.fillna(np.NaN)
    #ind = df[df['vorname'].isna() & df['nachname'].isna()].index.values
    #df.drop(ind,inplace=True)
    return df

In [3]:
path_presentation = 'old_database/database_mod.talks'
df_presentation = read_addresses(path_presentation)


In [4]:
df_presentation.columns

Index(['invited', 'type', 'nonmiei', 'host', 'year', 'month', 'day', 'where',
       'title', 'speaker', 'abstract', 'dayname', 'department', 'hostref',
       'hour', 'invitedby', 'invitedfor', 'speakerref', 'talkabstract', '',
       'und', 'room', 'molecular'],
      dtype='object')

**Write to Django Database**

In [5]:
for index, row in df_presentation.iterrows():
    comment_date_raw_l=[]
    no_speaker=False
    if type(row['year'])!= float: # or row['year']!='':
        year_raw=row['year']
        year_list=year_raw.split('-')
        year_start_raw=year_list[0]
        year_end_raw=year_list[-1]
    else:
        year_raw=None
    if type(row['month'])!=float: # or row['month']!='':
        month_raw=row['month']
        month_list=month_raw.split('-')
        month_start_raw=month_list[0]
        month_end_raw=month_list[-1]
        if month_start_raw=='':
            month_start_raw='01'
            month_end_raw='01'
            comment_date_raw_l.append('Unknown month')
    else:
        month_start_raw='01'
        month_end_raw='01'
        comment_date_raw_l.append('Unknown month')
    if type(row['day'])!=float: # or row['days']!='':
        day_raw=row['day']
        day_list=day_raw.split('-')
        day_start_raw=day_list[0]
        day_end_raw=day_list[-1]
        for c_str in day_end_raw:
            if '(' == c_str:
                print('jolo')
                temp_l=day_end_raw.split('(')
                print('temp_l',temp_l)
                day_end_raw=temp_l[0]
                month_end_raw=temp_l[1].strip(')')
        if day_start_raw=='':
            day_start_raw='01'
            day_end_raw='01'
            comment_date_raw_l.append('Unknown day')
    else:
        day_start_raw='01'
        day_end_raw='01'
        comment_date_raw_l.append('Unknown day')
    if type(row['hour'])!=float: # or row['days']!='':
        try:
            int(row['hour'][0].strip())
            hour_raw=row['hour']
            hour_list=hour_raw.split('-')
            time_start_raw=hour_list[0].strip()
            time_end_raw=hour_list[-1].strip()
        except:
            time_start_raw=None
            time_end_raw=None
    else:
        time_start_raw=None
        time_end_raw=None
    public_raw=True
    if row['title']!=float:
        title_raw = html.unescape(row['title'])
    else:
        title_raw=None
    if type(row['nonmiei'])!=float:
        if row['nonmiei']=='no' or row['nonmiei']=='No' or row['nonmiei']=='NO':
            nonmiei_raw=False
        else:
            nonmiei_raw=True
    else:
        nonmiei_raw=False
    if type(row['hostref'])!=float:
        #copyright_raw=row['url']
        host_url_raw=row['hostref']
    else:
        host_url_raw=None
    if type(row['invitedby'])!=float:
        host_person_raw=html.unescape(row['invitedby'])
    else:
        host_person_raw=None
    if type(row['host'])!=float:
        host_university_raw=html.unescape(row['host'])
    else:
        host_university_raw=None
    if type(row['speaker'])!=float:
        author_ids_l=[]
        if ' and ' in html.unescape(row['speaker']):
            print('yes')
            row['speaker']=row['speaker'].replace(' and ',',')
        firstSplit_l=html.unescape(row['speaker']).split(',')

        for c_split in range(0,len(firstSplit_l)):
            print('firstSplit_l',firstSplit_l)
            try:
                mem_id = Member.objects.filter(last_name__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>'))[0].id
            except:
                #if mem_id==None:
                print('mem_id is none')
                try:
                    mem_id = Member.objects.filter(last_name_alt__contains=html.unescape(firstSplit_l[c_split]).split(' ')[-1].strip('</u>'))[0].id
                except:
                    mem_id=None
                    continue
            print(mem_id,type(mem_id))
            author_ids_l.append(mem_id)
            print(mem_id,'SPEAKER')
        speaker_char_raw=html.unescape(row['speaker'])
        if len(author_ids_l)==0:
            no_speaker=True
    if type(row['invitedfor'])!=float:
        event_title_raw=html.unescape(row['invitedfor'])
    else:
        event_title_raw=None
    if type(row['where'])!=float:
        location_raw=html.unescape(row['where'])
    else:
        location_raw=None
    if type(row['type'])!=float:
        presentation_type_raw=html.unescape(row['type'])
        presentation_type_alt_raw=None
    else:
        presentation_type_raw=None
        presentation_type_alt_raw=None
    if type(row['department'])!=float:
        host_department_raw=html.unescape(row['department'])
    else:
        host_department_raw=None
    if type(row['talkabstract'])!=float:
        abstract_raw=html.unescape(row['talkabstract'])
    elif type(row['abstract'])!=float:
        abstract_raw=html.unescape(row['abstract'])
    else:
        abstract_raw=None
    if type(row['room'])!=float:
        room_raw=html.unescape(row['room'])
    else:
        room_raw=None
    date_start_raw = f"{year_start_raw}-{month_start_raw}-{day_start_raw}"
    date_end_raw = f"{year_end_raw}-{month_end_raw}-{day_end_raw}"
    print('host_university_raw',host_university_raw)
    print('time_raw',time_start_raw,time_end_raw)
    print('date_start_raw',date_start_raw)
    print('title',title_raw)
    if len(comment_date_raw_l)!=0:
        comment_date_raw=''.join(comment_date_raw_l)
    else:
        comment_date_raw=None
    try:
        if "workshop" in event_title_raw:
            print(event_title_raw)
            event_type_raw=Event_type.objects.get(id=3)
        elif "conference" in event_title_raw:
            event_type_raw=Event_type.objects.get(id=1)
        else:
            event_type_raw=Event_type.objects.get(id=2)
    except:
        print("no title?",event_title_raw)
        event_type_raw=Event_type.objects.get(id=2)
        pass
    try:
        if "colloquium" in presentation_type_raw:
            print(presentation_type_raw)
            presentation_type_raw=Presentation_type.objects.get(id=2)
        if "Colloquium" in presentation_type_raw:
            print(presentation_type_raw)
            presentation_type_raw=Presentation_type.objects.get(id=2)
        elif "Kolloquium" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=2)
        elif "kolloquium" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=2)
        elif "seminar" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=1)
        elif "Seminar" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=1)
        elif "poster" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=3)
        elif "Poster" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=3)
        elif "talk" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=4)
        elif "Talk" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=4)
        elif "invited" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=5)
        elif "Invited" in presentation_type_raw:
            presentation_type_raw=Presentation_type.objects.get(id=5)
        else:
            presentation_type_alt_raw=presentation_type_raw
            presentation_type_raw=None
            if presentation_type_alt_raw!=None:
                if "??" in presentation_type_alt_raw:
                    presentation_type_alt_raw=None
    except:
        presentation_type_alt_raw=presentation_type_raw
        presentation_type_raw=None
        if presentation_type_alt_raw!=None:
            if "??" in presentation_type_alt_raw:
                    presentation_type_alt_raw=None
        pass
    new_presentation = Presentation(    
                        start_date=date_start_raw,
                            end_date=date_end_raw,
                            comment_date=comment_date_raw,
                          title=title_raw,
                            nonmiei=nonmiei_raw,
                            author_char=speaker_char_raw,
                            start_time=time_start_raw,
                            end_time=time_end_raw,
                          host_department=host_department_raw,
                            presentation_type=presentation_type_raw,
                            presentation_type_alt=presentation_type_alt_raw,
                            location=location_raw,
                            event_type=event_type_raw,
                            event_title=event_title_raw,
                            host_university=host_university_raw,
                            host_person=host_person_raw,
                            host_url=host_url_raw,
                          abstract=abstract_raw)
   
    new_presentation.save()
    if not no_speaker:
       for c_ids in range(0,len(author_ids_l)):
           if c_ids==0:
                new_presentation.author.add(author_ids_l[c_ids])
           else:
                new_presentation.presentor.add(author_ids_l[c_ids])
    time.sleep(0.25)

firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw UC Berkley
time_raw None None
date_start_raw 2019-08-12
title Reprogrammable materials
no title? None
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw The Shanghai Jiao Tong University
time_raw None None
date_start_raw 2019-05-16
title Materials 4.0: The age of cognitive materials
no title? None
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Denmark University of Technology
time_raw None None
date_start_raw 2019-02-15
title Sensing at the quantum limit
no title? None
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw University of Jinan
time_raw None None
date_start_raw 2018-09-18
title Sensing towards the quantum limit: The convergence of molecular detection and artificial perceptrons
no title? None
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
ho

firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Technischen Sammlungen Dresden, Max-Planck-Institut für molekulare Zellbiologie
time_raw None None
date_start_raw 2014-12-02
title Nanotechnology, Heimat and all that jazz...
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Ambrosetti Technology Forum 2014 - Innovation, Education, Entrepreneurship; Castel Brando
time_raw 09:00 10:30
date_start_raw 2014-05-24
title Innovation culture in Korea and Germany: different shots on the same goal.
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw EMM-NANO
time_raw 10:00 10:45
date_start_raw 2014-04-25
title TU Dresden. The Synergetic University
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Horizon2020
time_raw None None
date_start_raw 2014-02-14
title HORIZON 2020 - Consortium meeting
firstSplit_l ['Gianaurelio Cuniberti']
2429 <c

firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw TU Dresden, Faculty of Science
time_raw 16:40 16:40
date_start_raw 2010-06-15
title Molecular Electronics: In weiter Ferne, so nah!
no title? None
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Forschungszentrum Dresden-Rossendorf
time_raw 12:00 12:00
date_start_raw 2010-04-22
title Molecular Electronics: In weiter Ferne, so nah!
no title? None
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Novalisforum Freiberg (Katholische Akademie im Bistum Dresden-Meißen)
time_raw 20:00 20:00
date_start_raw 2009-12-02
title Immer kleiner, immer großartiger - Nanotechnologie für die Zukunft
no title? None
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw IFW Dresden
time_raw 10:45 10:45
date_start_raw 2009-10-13
title Nanotechnologie - Grosse Ambitionen fuer das unendlich Kleine (<b>

firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Technical University of Dresden, Dresden, Germany
time_raw 14:00 14:00
date_start_raw 2006-02-06
title Nanoelectronics: Challenges for Theory (<b>colloquium talk</b>)
Colloquium
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Linkoeping University, Linkoeping, Sweden
time_raw None None
date_start_raw 2006-01-26
title Contact dependence of carrier injection in carbon nanotubes
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw Technical University of Chemnitz, Chemnitz, Germany
time_raw None None
date_start_raw 2006-01-09
title New materials for nanoelectronics: Computational challenges (<b>colloquium talk</b>)
Colloquium
firstSplit_l ['Gianaurelio Cuniberti']
2429 <class 'int'>
2429 SPEAKER
host_university_raw University of Ulm, Ulm, Germany
time_raw 14:00 14:30
date_start_raw 2005-12-22
title Molecular Electronics

Old stuff:

In [ ]:
int('    ')